In [223]:
# import os
import json
from collections import defaultdict
import gzip
import pandas as pd
from lxml import html,etree
# from BeautifulSoup4 import UnicodeDammit
import numpy as np

# from urllib.request import urlopen

In [224]:
#!wget https://datarepo.eng.ucsd.edu/mcauley_group/data/amazon_v2/categoryFilesSmall/AMAZON_FASHION_5.json.gz
# Even if we use the link above, it will download the file to the local machine. So I put the file in the same directory as the notebook

In [225]:
# Data is in the format: 
# "overall": 4.0,
# "verified",
# "reviewTime",
# "reviewerID",
# "asin",
# "style": {"Format:"}
# "reviewerName",
# "reviewText"
# "summary",
# "unixReviewTime"

### load the meta data
data = []
with gzip.open('Dataset/meta_Software.json.gz') as f:
    for l in f:
        data.append(json.loads(l.strip()))
    
# total length of list, this number equals total number of products
print("Total number of items in the dataset: ", len(data))

# first row of the list
print(data[0])

Total number of items in the dataset:  26790
{'category': [], 'tech1': '', 'description': [], 'fit': '', 'title': 'HOLT PHYSICS LESSON PRESENTATION CD-ROM QUICK CONCEPTS', 'also_buy': [], 'tech2': '', 'brand': 'HOLT. RINEHART AND WINSTON', 'feature': [], 'rank': '25,550 in Software (', 'also_view': [], 'main_cat': 'Software', 'similar_item': '', 'date': '</div>', 'price': '.a-box-inner{background-color:#fff}#alohaBuyBoxWidget .selected{background-color:#fffbf3;border-color:#e77600;box-shadow:0 0 3px rgba(228,121,17,.5)}#alohaBuyBoxWidget .contract-not-available{color:gray}#aloha-cart-popover .aloha-cart{height:auto;overflow:hidden}#aloha-cart-popover #aloha-cartInfo{float:left}#aloha-cart-popover #aloha-cart-details{float:right;margin-top:1em}#aloha-cart-popover .deviceContainer{width:160px;float:left;padding-right:10px;border-right:1px solid #ddd}#aloha-cart-popover li:last-child{border-right:0}#aloha-cart-popover .aloha-device-title{height:3em;overflow:hidden}#aloha-cart-popover .alo

In [226]:
# convert list into pandas dataframe

df = pd.DataFrame.from_dict(data)

print(len(df))
print(df)


pd.set_option('display.max_colwidth', 300)
pd.set_option('display.max_rows', 20 )

26790
                                                                                                                                                                                                                                                                                                          category  \
0                                                                                                                                                                                                                                                                                                               []   
1                                                                                                                                                                                                                                                                                                               []   
2                                                               

In [227]:
### load the for "Software" category:

data2 = []
with gzip.open('Dataset/meta_Software.json.gz') as f:
    for l in f:
        data2.append(json.loads(l.strip()))
    
# total length of list, this number equals total number of products
print("Total number of items in the dataset: ", len(data2))


Total number of items in the dataset:  26790


In [228]:
# convert list into pandas dataframe

df2 = pd.DataFrame.from_dict(data2)

# Features of the dataset
df2.columns

# Features are slightly different than 


Index(['category', 'tech1', 'description', 'fit', 'title', 'also_buy', 'tech2',
       'brand', 'feature', 'rank', 'also_view', 'main_cat', 'similar_item',
       'date', 'price', 'asin', 'imageURL', 'imageURLHighRes', 'details'],
      dtype='object')

In [229]:
df2.head()

category tech1  \
0       []         
1       []         
2       []         
3       []         
4       []         

                                                                                                                                                                                                                                                                                                   description  \
0                                                                                                                                                                                                                                                                                                           []   
1  [, <b>Latin rhythms that will get your kids singing in Spanish</b>, <i>Sing, Watch, and Learn Spanish</i> helps your kids ages four through eight take a giant step in learning Spanish by combining two time-honored methods kids have always used to develop their language skills: Imitating other ki...   
2  [<b>Connect is the only integrated learning system that empowers students by continuously adapting to deliver precisely what they need, when they need it, how they need it, so that your class time is more engaging and effective.</b><br />, Kelly Cowan just celebrated her 20th anniversary at Miam...   
3                                                                                                                                                                                                                                                                                                           []   
4  [<i>Anatomy &amp; Physiology Revealed Cat</i> is the ultimate online interactive cat dissection experience. This state-of-the-art program uses cat photos combined with a layering technique that allows the student to peel away layers of the cat to reveal structures beneath the surface. <i>Anatomy...   

  fit  \
0       
1       
2       
3       
4       

                                                                                                    title  \
0                                                  HOLT PHYSICS LESSON PRESENTATION CD-ROM QUICK CONCEPTS   
1  Sing, Watch, &amp; Learn Spanish (DVD + Guide): 16 Fun Music Videos to Introduce Your Child to Spanish   
2                  Connect with LearnSmart Access Card for Microbiology Fundamentals: A Clinical Approach   
3                                        LearnSmart Standalone Access Card for Prescott's Microbiology 9e   
4                                     Anatomy &amp; Physiology Revealed Student Access Card (Cat Version)   

                               also_buy tech2  \
0                                    []         
1                                    []         
2                                    []         
3                                    []         
4  [0323394612, 0323227937, 1118527488]         

                                  brand feature                  rank  \
0            HOLT. RINEHART AND WINSTON      []  25,550 in Software (   
1                           McGraw Hill      []  15,792 in Software (   
2  McGraw-Hill Science/Engineering/Math      []  16,900 in Software (   
3                 McGraw-Hill Education      []  12,986 in Software (   
4                 McGraw-Hill Education      []  14,861 in Software (   

  also_view  main_cat similar_item    date  \
0        []  Software               </div>   
1        []  Software               </div>   
2        []  Software               </div>   
3        []  Software               </div>   
4        []  Software               </div>   

                                                                                                                                                                                                                                                                                                         price  \
0  .a-box-inner{b

In [230]:
# Some products have multiple descriptions containing information of for instance the author.
# Perhaps only the first description string should be analyzed for our purpose? This seems to be primarily for the product.
# For now i have just merged all descriptions into a single string for analysis.

#df2.description = df2.description.apply(lambda x: "".join(x))

# Drop rows with no description (empty list)
df2 = df2[df2['description'].map(lambda d: len(d)) > 0]



# df2.description


In [231]:

df2.description = df2.description.apply(lambda x: [string for string in x if string != ""])


In [232]:
for i in range(3):

    print(df2.iloc[i].description[0])

<b>Latin rhythms that will get your kids singing in Spanish</b>
<b>Connect is the only integrated learning system that empowers students by continuously adapting to deliver precisely what they need, when they need it, how they need it, so that your class time is more engaging and effective.</b><br />
<i>Anatomy &amp; Physiology Revealed Cat</i> is the ultimate online interactive cat dissection experience. This state-of-the-art program uses cat photos combined with a layering technique that allows the student to peel away layers of the cat to reveal structures beneath the surface. <i>Anatomy &amp; Physiology Revealed Cat</i> also offers animations, histologic and radiologic imaging, audio pronunciations, and comprehensive quizzing. It can be used as part of any one or two semester undergraduate anatomy &amp; physiology or human anatomy course; <i>Anatomy &amp; Physiology Revealed Cat</i> is available stand-alone, or can be combined with any McGraw-Hill book.


In [233]:
df2.description = df2.description.apply(lambda x: ". ".join(x))




In [234]:
df2.loc[1:4]

category tech1  \
1       []         
2       []         
4       []         

                                                                                                                                                                                                                                                                                                   description  \
1  <b>Latin rhythms that will get your kids singing in Spanish</b>. <i>Sing, Watch, and Learn Spanish</i> helps your kids ages four through eight take a giant step in learning Spanish by combining two time-honored methods kids have always used to develop their language skills: Imitating other kids ...   
2  <b>Connect is the only integrated learning system that empowers students by continuously adapting to deliver precisely what they need, when they need it, how they need it, so that your class time is more engaging and effective.</b><br />. Kelly Cowan just celebrated her 20th anniversary at Miami...   
4  <i>Anatomy &amp; Physiology Revealed Cat</i> is the ultimate online interactive cat dissection experience. This state-of-the-art program uses cat photos combined with a layering technique that allows the student to peel away layers of the cat to reveal structures beneath the surface. <i>Anatomy ...   

  fit  \
1       
2       
4       

                                                                                                    title  \
1  Sing, Watch, &amp; Learn Spanish (DVD + Guide): 16 Fun Music Videos to Introduce Your Child to Spanish   
2                  Connect with LearnSmart Access Card for Microbiology Fundamentals: A Clinical Approach   
4                                     Anatomy &amp; Physiology Revealed Student Access Card (Cat Version)   

                               also_buy tech2  \
1                                    []         
2                                    []         
4  [0323394612, 0323227937, 1118527488]         

                                  brand feature                  rank  \
1                           McGraw Hill      []  15,792 in Software (   
2  McGraw-Hill Science/Engineering/Math      []  16,900 in Software (   
4                 McGraw-Hill Education      []  14,861 in Software (   

  also_view  main_cat similar_item    date  price        asin  \
1        []  Software               </div>         0071480935   
2        []  Software               </div>         007329506X   
4        []  Software               </div>  $4.83  0073525758   

                                                                                      imageURL  \
1  [https://images-na.ssl-images-amazon.com/images/I/51BtLn2-L-L._SX38_SY50_CR,0,0,38,50_.jpg]   
2  [https://images-na.ssl-images-amazon.com/images/I/51z1MKLSD3L._SX38_SY50_CR,0,0,38,50_.jpg]   
4  [https://images-na.ssl-images-amazon.com/images/I/51Do0BbcTkL._SX38_SY50_CR,0,0,38,50_.jpg]   

                                                      imageURLHighRes details  
1  [https://images-na.ssl-images-amazon.com/images/I/51BtLn2-L-L.jpg]     NaN  
2  [https://images-na.ssl-images-amazon.com/images/I/51z1MKLSD3L.jpg]     NaN  
4  [https://images-na.ssl-images-amazon.com/images/I/51Do0BbcTkL.jpg]     NaN

In [235]:
# A lot of the descriptions (and other features) contain HTML.
# The function parses and "translates" into plain text descriptions more suitable for analysis

def strip_html(s):
    if not s or s.isspace(): 
        return ''
    try:
        return str(html.fromstring(s).text_content())
    except etree.ParserError: # I am not able to find out why the error occur so i continued by catching the exception. Seem to happen on some empty description strings 
        return ''

# df2.iloc[0].description = strip_html(df2.iloc[0].description)
df2.description = df2.description.apply(lambda x: strip_html(x))
df2.iloc[0:2]
# df2.loc[0:2]

dfdescription = df2.description
len(dfdescription.iloc[0])

758

In [243]:
descr = defaultdict(list)
 
for idx, row in df2.iterrows():
    if row.description in descr[row.asin]:
        print(idx, row.asin, row.description)
    else:
        descr[row.asin].append(row.description)



6028 B00000IV94 SET the Computer Game shares the game features of the world famous SET Game. The computer version offers up to ten players the opportunity to play together on one computer or solitaire or against the computer.. The object of the game is to identify sets of three cards. Each card is unique in its four features: number: 1,2, or 3; symbol: diamond, squiggle, or oval; shading: solid, striped, or open; and color: red, green, or purple. A set consists of three cards on which every feature is either the same on all of the cards, or different on all of the cards.
6029 B00000IWIZ Star Wars Episode I: The Gungan Frontier is the first ever Star Wars ecological simulation game designed for players 10 and older. Taking place during the Episode I time period, players must transform the barren moon of Naboo into a thriving, balanced ecosystem and help the Gungans build a new underwater bubble city. From their Mantaris Amphibious Transport, player control the release of fantastic creat

In [237]:
descr

defaultdict(list,
            {'0071480935': ['Latin rhythms that will get your kids singing in Spanish. Sing, Watch, and Learn Spanish helps your kids ages four through eight take a giant step in learning Spanish by combining two time-honored methods kids have always used to develop their language skills: Imitating other kids and singing along with simple melodies. This charming DVD contains 16 music videos featuring kids engaged in fun activities, from visiting animals at the zoo to comparing clothing sizes in grandmas closet.. Each video features an original song of authentic Latin rhythms that gets kids singing along with the children on screen. As they watch, listen, and sing along, kids absorb 300 Spanish words, each of which is shouted out in a song and displayed as a subtitle on screen.'],
             '007329506X': ['Connect is the only integrated learning system that empowers students by continuously adapting to deliver precisely what they need, when they need it, how they ne

In [238]:
for key, value in descr.items():
    print(type(value))
    # if len(elem.values())  >1:
    #     print(elem)d
    

<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'list'>
<class 'li

In [239]:
display(descr

SyntaxError: '(' was never closed (568357130.py, line 1)

In [ ]:
def shingle(aString, q, delimiter=' '):
    """
    Input:
        - aString (str): string to split into shingles
        - q (int)
        - delimiter (str): string of the delimiter to consider to split the input string (default: space)
    Return: list of unique shingles
    """
    all_shingles = []
    if delimiter != '':
        words_list = aString.split(delimiter)
    else:
        words_list = aString
    for i in range (len(words_list)-q+1):
        all_shingles.append(delimiter.join(words_list[i:i+q]))
    return list(set(all_shingles))

In [ ]:
ex_string, q = dfdescription.iloc[0], 2
# ex_string, q = "Latin rhythms that will get your kids singing in Spanish. ", 2
ex_shingles = shingle(ex_string, q)
# assert len(ex_shingles) == 7
print('\nInitial string:', ex_string)
print(f'>> Shingles with q = {q} :',ex_shingles)


Initial string: Latin rhythms that will get your kids singing in Spanish. Sing, Watch, and Learn Spanish helps your kids ages four through eight take a giant step in learning Spanish by combining two time-honored methods kids have always used to develop their language skills: Imitating other kids and singing along with simple melodies. This charming DVD contains 16 music videos featuring kids engaged in fun activities, from visiting animals at the zoo to comparing clothing sizes in grandmas closet.. Each video features an original song of authentic Latin rhythms that gets kids singing along with the children on screen. As they watch, listen, and sing along, kids absorb 300 Spanish words, each of which is shouted out in a song and displayed as a subtitle on screen.
>> Shingles with q = 2 : ['along with', 'which is', 'have always', 'watch, listen,', 'is shouted', 'of which', 'Spanish helps', 'they watch,', 'animals at', 'learning Spanish', 'kids engaged', 'authentic Latin', 'used to', '

In [ ]:
print(len(dfdescription))
dfdescription.drop_duplicates(inplace=True)
print(len(dfdescription))
# dfdescription

23195
17272


In [ ]:
# Applying strip_html to description
# df2['description'] = df2['description'].apply(strip_html)


In [ ]:
df2.head()

category tech1  \
1       []         
2       []         
4       []         
5       []         
6       []         

                                                                                                                                                                                                                                                                                                   description  \
1  Latin rhythms that will get your kids singing in Spanish. Sing, Watch, and Learn Spanish helps your kids ages four through eight take a giant step in learning Spanish by combining two time-honored methods kids have always used to develop their language skills: Imitating other kids and singing al...   
2  Connect is the only integrated learning system that empowers students by continuously adapting to deliver precisely what they need, when they need it, how they need it, so that your class time is more engaging and effective.. Kelly Cowan just celebrated her 20th anniversary at Miami University M...   
4  Anatomy & Physiology Revealed Cat is the ultimate online interactive cat dissection experience. This state-of-the-art program uses cat photos combined with a layering technique that allows the student to peel away layers of the cat to reveal structures beneath the surface. Anatomy & Physiology R...   
5  John Coburn grew up in the Hawaiian Islands, the seventh of sixteen children. He received his Associate of Arts degree in 1977 from Windward Community College, where he graduated with honors. In 1979 he received a Bachelors Degree in Education from the University of Hawaii. After being lured int...   
6  Connect is the only integrated learning system that empowers students by continuously adapting to deliver precisely what they need, when they need it, how they need it, so that your class time is more engaging and effective.. Kelly Cowan just celebrated her 20th anniversary at Miami University M...   

  fit  \
1       
2       
4       
5       
6       

                                                                                                    title  \
1  Sing, Watch, &amp; Learn Spanish (DVD + Guide): 16 Fun Music Videos to Introduce Your Child to Spanish   
2                  Connect with LearnSmart Access Card for Microbiology Fundamentals: A Clinical Approach   
4                                     Anatomy &amp; Physiology Revealed Student Access Card (Cat Version)   
5                               Connect Math by ALEKS Access Card 52 Weeks for College Algebra Essentials   
6                                  Connect Access Card for Microbiology Fundamentals: A Clinical Approach   

                               also_buy tech2  \
1                                    []         
2                                    []         
4  [0323394612, 0323227937, 1118527488]         
5                                    []         
6                                    []         

                                         brand                        feature  \
1                                  McGraw Hill                             []   
2         McGraw-Hill Science/Engineering/Math                             []   
4                        McGraw-Hill Education                             []   
5         McGraw-Hill Science/Engineering/Math                             []   
6  Brand: McGraw-Hill Science/Engineering/Math  [Used Book in Good Condition]   

                   rank  \
1  15,792 in Software (   
2  16,900 in Software (   
4  14,861 in Software (   
5  43,708 in Software (   
6   8,512 in Software (   

                                                                              also_view  \
1                                                                                    []   
2                                                                                    []   
4                                                                                    []   
5                        

In [ ]:
# Merge description to reviews data using 'asin'

merged_df = df.merge(df2[['asin', 'description']], on='asin', how='left')

In [ ]:
merged_df.iloc[15:200]

category  \
15                                       []   
16                                       []   
17                                       []   
18                                       []   
19                                       []   
..                                      ...   
195   [Software, Education &amp; Reference]   
196   [Software, Education &amp; Reference]   
197  [Software, Children's, Early Learning]   
198  [Software, Children's, Early Learning]   
199   [Software, Education &amp; Reference]   

                                                                                                                                                                                                                                                                                                           tech1  \
15                                                                                                                                                                                                                                                                                                                 
16                                                                                                                                                                                                                                                                                                                 
17                                                                                                                                                                                                                                                                                                                 
18                                                                                                                                                                                                                                                                                                                 
19                                                                                                                                                                                                                                                                                                                 
..                                                                                                                                                                                                                                                                                                           ...   
195   class="a-keyvalue prodDetTable" role="presentation">\n         \n           \n           \n           \n           <tbody><tr>\n            \n            \n              \n              \n               \n                <th class="a-color-secondary a-size-base prodDetSectionEntry">\n          ...   
196   class="a-keyvalue prodDetTable" role="presentation">\n         \n           \n           \n           \n           <tbody><tr>\n            \n            \n              \n              \n               \n                <th class="a-color-secondary a-size-base prodDetSectionEntry">\n          ...   
197                                                                                                                                                                                                                                                                                                                
198   class="a-keyvalue prodDetTable" role="presentation">\n         \n           \n           \n           \n           <tbody><tr>\n            \n            \n              \n              \n               \n                <th class="a-color-secondary a-size-base prodDetSectionEntry">\n          ...   
199   class="a-keyvalue prodDetTable" role="presentation">\n         \n           